In [9]:
import re
from tqdm.auto import trange, tqdm

def label_lines_refined(text, show_progress=False):
    lines = text.split("\n")
    labeled_lines = []
    continuation_pattern = re.compile(r'(?<=[a-z0-9,\'"])$(?!\n\n)', flags=re.MULTILINE)
    exclusion_pattern = re.compile(r"(Mr|Mrs|Dr|Ms)\.$|^\*|^\d+\.", flags=re.MULTILINE)
    likely_continuation_pattern = re.compile(r"(,|and|or|with)$", flags=re.MULTILINE)
    incomplete_sentence_pattern = re.compile(r"(?<=[a-z])\.$", flags=re.MULTILINE)

    for i in trange(len(lines) - 1, disable=not show_progress):
        current_line = lines[i].strip()
        next_line = lines[i + 1].strip()

        if exclusion_pattern.search(current_line) or exclusion_pattern.search(next_line):
            labeled_lines.append({"text": current_line, "label": 0})
            continue

        if (
            likely_continuation_pattern.search(current_line)
            or incomplete_sentence_pattern.search(current_line)
            or (
                continuation_pattern.search(current_line)
                and next_line
                and (next_line[0].islower() or next_line.split()[0].istitle())
            )
        ):
            labeled_lines.append({"text": current_line, "label": 1})
        else:
            labeled_lines.append({"text": current_line, "label": 0})

    labeled_lines.append({"text": lines[-1].strip(), "label": 0})
    return labeled_lines

def reconstruct_text(labeled_lines):
    reconstructed_text = ""
    for i in range(len(labeled_lines)):
        line = labeled_lines[i]["text"]
        label = labeled_lines[i]["label"]

        if label == 1 and i + 1 < len(labeled_lines):
            # Append the current line without a newline if it's incorrectly split
            reconstructed_text += line + " "
        else:
            # Append the current line with a newline
            reconstructed_text += line + "\n"

    return reconstructed_text.strip()  # Remove any trailing newline characters


# Example usage
example_text = """
the words "May I
come in?" should be on one line
"""

labeled_example_refined = label_lines_refined(example_text)
reconstructed_text = reconstruct_text(labeled_example_refined)
print(reconstructed_text)

# def fix_newlines_v2(example, text_column: str = "text"):

#     labeled_text = label_lines_refined(str(example[text_column]))
#     return {text_column: reconstruct_text(labeled_text)}


# ds_fnv2 = dataset.map(fix_newlines_v2, num_proc=6)
# ds_fnv2

the words "May I
come in?" should be on one line


this ^ does not work because it depends on having more text/puncatuation than that short example

In [10]:
longer_example = """[Illustration: THE GIRL'S OWN PAPER

VOL. XX.--NO. 990.] DECEMBER 17, 1898. [PRICE ONE PENNY.]

"OUR HERO."

BY AGNES GIBERNE, Author of "Sun, Moon and Stars," "The Girl at the
Dower House," etc.

[Illustration: "THE HORSES IN QUESTION WERE SOMEWHAT SORRY BEASTS."]

_All rights reserved._]

CHAPTER XII.

ORDERED TO VERDUN.

"Mamma! Mother!" cried Roy, bursting into the sitting-room at
Fontainebleau one wintry day. "Ma'am, what do you think?"

Roy had by this time quite recovered from his illness, though his face still bore evidence of the same in the shape of several small red pits, which had not yet had time to lose their prominence. His eyes sparkled with excitement. Mrs. Baron was on the sofa, resting after a walk with her husband, and Colonel Baron sat near, book in hand. Ivor, who happened to be in rear of them both, made a silencing gesture, but Roy was much too eager to attend, or to read his meaning.

"Only think, ma'am. Do but hear! All of us are ordered off from
Fontainebleau"""


print(reconstruct_text(label_lines_refined(longer_example)))

[Illustration: THE GIRL'S OWN PAPER

VOL. XX.--NO. 990.] DECEMBER 17, 1898. [PRICE ONE PENNY.]

"OUR HERO."

BY AGNES GIBERNE, Author of "Sun, Moon and Stars," "The Girl at the Dower House," etc. 
[Illustration: "THE HORSES IN QUESTION WERE SOMEWHAT SORRY BEASTS."]

_All rights reserved._]

CHAPTER XII.

ORDERED TO VERDUN.

"Mamma! Mother!" cried Roy, bursting into the sitting-room at Fontainebleau one wintry day. "Ma'am, what do you think?"

Roy had by this time quite recovered from his illness, though his face still bore evidence of the same in the shape of several small red pits, which had not yet had time to lose their prominence. His eyes sparkled with excitement. Mrs. Baron was on the sofa, resting after a walk with her husband, and Colonel Baron sat near, book in hand. Ivor, who happened to be in rear of them both, made a silencing gesture, but Roy was much too eager to attend, or to read his meaning. 
"Only think, ma'am. Do but hear! All of us are ordered off from Fontainebleau

In [12]:
ex2 = """CHAPTER III.

"You sought to prove how I could love,
And my disdain is my reply."

_Tennyson._

Linnaea's first waking thoughts carried with them the conviction that life was different--why was it? Ah, she remembered! Last night's scene came back to her with a rush of feeling that brought the warm colour to her face. Then came the colder and more prosaic feelings which so often come with the morning. Gwendoline would soon be like the others--she would go over to the popular opinion, and Linnaea would be thrust upon her own companionship as before. These thoughts were passing through her mind when she heard a tap at the door, and a voice called, "May I
come in?"

Linnaea opened the door, and there stood Gwendoline, her arms full of knick-knacks of all sorts.

"You are only dressing! I have been

"""

print(reconstruct_text(label_lines_refined(ex2)))

CHAPTER III.

"You sought to prove how I could love, And my disdain is my reply."

_Tennyson._

Linnaea's first waking thoughts carried with them the conviction that life was different--why was it? Ah, she remembered! Last night's scene came back to her with a rush of feeling that brought the warm colour to her face. Then came the colder and more prosaic feelings which so often come with the morning. Gwendoline would soon be like the others--she would go over to the popular opinion, and Linnaea would be thrust upon her own companionship as before. These thoughts were passing through her mind when she heard a tap at the door, and a voice called, "May I
come in?"

Linnaea opened the door, and there stood Gwendoline, her arms full of knick-knacks of all sorts. 
"You are only dressing! I have been
